# Lesson 16: PCA + ICA (Cocktail Party) — **Simple ICA via Gradient Ascent (NumPy)**

This notebook follows Andrew Ng’s **PCA + ICA** lecture flow:

- **Part A (PCA)**: PCA in *pure NumPy* (covariance, eigendecomposition / SVD, projection, reconstruction).
- **Part B (ICA)**: The **cocktail party** setup and a **very simple ML/gradient-ascent ICA** (no FastICA).
- **Part C (Audio demo)**: Pick one **professor** wav and one **student** wav, create a *two-microphone mixture*, then recover the two sources with ICA.  
  Finally, we **play audio in-notebook**.

> Notes  
> - ICA needs *at least as many mixtures (“microphones”) as sources*.  
> - If you only have **one** mixed recording, ICA can’t uniquely separate two speakers.  
>   So we **simulate two microphones** by mixing the two clean signals through a 2×2 mixing matrix.

In [142]:
import os
import glob
import numpy as np
import matplotlib.pyplot as plt

from IPython.display import Audio, display

# Try to use scipy if available (common in most envs). If not, we fall back to the built-in wave module.
try:
    from scipy.io import wavfile
    SCIPY_WAV = True
except Exception:
    import wave
    SCIPY_WAV = False

np.random.seed(0)

## Helper: Load / Save WAV (robust, mono)

We standardize audio to:
- `float32` in `[-1, 1]`
- **mono**
- consistent length for mixing

In [143]:
def load_wav_mono(path):
    """Load a wav file as mono float32 in [-1, 1]. Returns (sr, x)."""
    if SCIPY_WAV:
        sr, x = wavfile.read(path)
        x = np.asarray(x)
        # Convert to float
        if x.dtype.kind in ("i", "u"):
            maxv = np.iinfo(x.dtype).max
            x = x.astype(np.float32) / maxv
        else:
            x = x.astype(np.float32)

        # stereo -> mono
        if x.ndim == 2:
            x = x.mean(axis=1).astype(np.float32)
        return sr, x

    # Fallback: wave module (16-bit PCM common)
    import wave
    with wave.open(path, "rb") as wf:
        sr = wf.getframerate()
        n = wf.getnframes()
        ch = wf.getnchannels()
        sampwidth = wf.getsampwidth()
        frames = wf.readframes(n)

    if sampwidth != 2:
        raise ValueError("wave fallback only supports 16-bit PCM WAVs (sampwidth=2).")

    x = np.frombuffer(frames, dtype=np.int16).astype(np.float32) / 32767.0
    if ch == 2:
        x = x.reshape(-1, 2).mean(axis=1)
    return sr, x

def save_wav(path, sr, x):
    """Save float audio [-1,1] to 16-bit PCM WAV."""
    x = np.asarray(x, dtype=np.float32)
    x = np.clip(x, -1.0, 1.0)
    x16 = (x * 32767.0).astype(np.int16)

    if SCIPY_WAV:
        from scipy.io import wavfile
        wavfile.write(path, sr, x16)
        return

    import wave
    with wave.open(path, "wb") as wf:
        wf.setnchannels(1)
        wf.setsampwidth(2)
        wf.setframerate(sr)
        wf.writeframes(x16.tobytes())

def list_wavs(folder):
    return sorted(glob.glob(os.path.join(folder, "*.wav")))

## Dataset paths (your local folder)

You said your audio lives here:

`data/mini-speech-diarization/versions/2/dataset/raw/`

with:
- `train/professor/*.wav` (7)
- `train/student/*.wav` (6)
- `valid/professor/*.wav` (2)
- `valid/student/*.wav` (2)

We’ll pick **one professor** and **one student** file (you can swap choices).

In [144]:
DATA_ROOT = "../data/mini-speech-diarization"

prof_train = os.path.join(DATA_ROOT, "train", "professor")
stud_train = os.path.join(DATA_ROOT, "train", "student")
prof_valid = os.path.join(DATA_ROOT, "valid", "professor")
stud_valid = os.path.join(DATA_ROOT, "valid", "student")

prof_files = list_wavs(prof_train)
stud_files = list_wavs(stud_train)

print("Professor train wavs:", len(prof_files))
print("Student train wavs:", len(stud_files))

# Choose which files to demo (change indices if you want)
prof_path = prof_files[0] if prof_files else None
stud_path = stud_files[0] if stud_files else None

print("Using professor:", prof_path)
print("Using student  :", stud_path)

Professor train wavs: 7
Student train wavs: 6
Using professor: ../data/mini-speech-diarization/train/professor/audio_1.wav
Using student  : ../data/mini-speech-diarization/train/student/audio_1.wav


## Load two clean sources and build a **two-mic** mixture

We create sources:

$$S(t) = \begin{bmatrix}s_1(t) \\\\ s_2(t)\end{bmatrix}$$

and simulate microphone recordings via a 2×2 mixing matrix:

$$X(t) = A \\, S(t)$$

So `X` has **2 channels** (mic1, mic2), and ICA tries to recover `S` from `X` up to permutation + scaling.

In [145]:
assert prof_path is not None and stud_path is not None, "Could not find professor/student WAV files in the expected folders."

sr1, s1 = load_wav_mono(prof_path)
sr2, s2 = load_wav_mono(stud_path)

if sr1 != sr2:
    raise ValueError(f"Sample rates differ: professor={sr1}, student={sr2}. Convert them to the same SR first.")

sr = sr1

# Match length (trim to the shorter)
n = min(len(s1), len(s2))
s1 = s1[:n]
s2 = s2[:n]

# Normalize each source (helps stability)
def rms(x): return np.sqrt(np.mean(x**2) + 1e-12)
s1 = s1 / (rms(s1) + 1e-9)
s2 = s2 / (rms(s2) + 1e-9)

S = np.vstack([s1, s2])  # shape (2, n)

# Mixing matrix (two microphones)
A = np.array([[1.0, 0.6],
              [0.4, 1.0]], dtype=np.float32)

X = A @ S  # shape (2, n)

# Make sure mixture is in a nice audible range
X = X / (np.max(np.abs(X)) + 1e-9)

print("S shape:", S.shape, "X shape:", X.shape)

/var/folders/dj/6n73kpm10ls582gfzn5ng6lm0000gn/T/ipykernel_42002/43144562.py:4: WavFileWarning: Chunk (non-data) not understood, skipping it.
  sr, x = wavfile.read(path)


### Listen: clean sources and mixed microphones

You should hear:
- **Source 1**: professor
- **Source 2**: student
- **Mic 1 / Mic 2**: mixed speech

In [146]:
# Professor (clean)
display(Audio(s1, rate=sr))

In [147]:
# Student (clean)
display(Audio(s2, rate=sr))

In [148]:
# Mic 1 (mixture)
display(Audio(X[0], rate=sr))

In [149]:
# Mic 2 (mixture)
display(Audio(X[1], rate=sr))


## (Quick) PCA Whitening in NumPy

Before ICA, we **center** and **whiten** the mixed signals so covariance is identity:

$$\tilde{X} = X - \mu$$

Compute covariance:

$$\Sigma = \frac{1}{n}\tilde{X}\tilde{X}^T$$

Eigendecompose:

$$\Sigma = U \Lambda U^T$$

Whitening transform:

$$X_{\text{white}} = \Lambda^{-1/2} U^T \\, \tilde{X}$$

In [150]:
def whiten(X):
    """Whiten X (shape: [mics, n]) to have identity covariance."""
    Xc = X - X.mean(axis=1, keepdims=True)
    n = Xc.shape[1]
    Sigma = (Xc @ Xc.T) / n
    eigvals, eigvecs = np.linalg.eigh(Sigma)  # for symmetric matrices
    # Sort descending
    idx = np.argsort(eigvals)[::-1]
    eigvals = eigvals[idx]
    eigvecs = eigvecs[:, idx]

    # Avoid divide-by-zero
    eps = 1e-9
    D_inv_sqrt = np.diag(1.0 / np.sqrt(eigvals + eps))
    Xw = D_inv_sqrt @ eigvecs.T @ Xc
    return Xw, (eigvecs, eigvals, X.mean(axis=1, keepdims=True))

Xw, whiten_info = whiten(X)

# Check covariance ~ I
Cov = (Xw @ Xw.T) / Xw.shape[1]
print("Whitened covariance:\n", Cov)

Whitened covariance:
 [[ 9.9999934e-01 -4.5450582e-07]
 [-4.5450582e-07  9.9999887e-01]]


## Simple ICA via Gradient Ascent

We learn an unmixing matrix `W` so that:

$$S \\approx W X_{white}$$

A common ML objective gives the update:

$$W \\leftarrow W + \\alpha\\left(W^{-T} + (1 - 2g(Wx))x^T\\right)$$

where:
$$g(u) = \\sigma(u) = \\frac{1}{1+e^{-u}}$$
- `x` is a **single** whitened sample (2×1)
- `α` is a small learning rate

This is intentionally **simple** (not FastICA).

In [151]:
def sigmoid(u):
    return 1.0 / (1.0 + np.exp(-u))

def ica_simple_gradient_ascent(Xw, lr=0.01, epochs=3, batch_size=2048, seed=0):
    """
    Xw: shape (m, n) whitened mixtures (m=2 here)
    Returns: W (m x m), S_hat (m x n)
    """
    rng = np.random.default_rng(seed)
    m, n = Xw.shape

    W = np.eye(m, dtype=np.float64)

    # We'll do mini-batches for speed/stability on audio-length signals.
    # Update uses the *average* over the batch.
    for ep in range(epochs):
        order = rng.permutation(n)

        for start in range(0, n, batch_size):
            idx = order[start:start+batch_size]
            Xb = Xw[:, idx]  # (m, B)

            U = W @ Xb                 # (m, B)
            G = sigmoid(U)             # (m, B)
            term = (1.0 - 2.0 * G)     # (m, B)

            # Average outer-products across batch:
            # (term @ Xb.T) / B gives an (m x m) matrix
            B = Xb.shape[1]
            grad = np.linalg.inv(W).T + (term @ Xb.T) / B

            W = W + lr * grad

        # quick monitor: keep W from blowing up
        detW = np.linalg.det(W)
        print(f"epoch {ep+1}/{epochs} | det(W)={detW:.4f} | ||W||_F={np.linalg.norm(W):.3f}")

    S_hat = W @ Xw
    return W, S_hat

W_hat, S_hat = ica_simple_gradient_ascent(Xw, lr=0.02, epochs=4, batch_size=4096)
print("W_hat:\n", W_hat)

epoch 1/4 | det(W)=2.5271 | ||W||_F=2.248
epoch 2/4 | det(W)=3.1636 | ||W||_F=2.515
epoch 3/4 | det(W)=3.4628 | ||W||_F=2.632
epoch 4/4 | det(W)=3.6093 | ||W||_F=2.687
W_hat:
 [[ 1.89811715  0.12014172]
 [-0.08339944  1.89623977]]


## Recover audio, fix scale, and listen

ICA recovers sources up to:
- **permutation** (which output is professor vs student)
- **scaling/sign** (volume flips)

We’ll:
1. Normalize each recovered component.
2. Choose an ordering by max correlation with the original sources (just for the demo).

In [152]:
def sigmoid(u):
    return 1.0 / (1.0 + np.exp(-u))

def sym_decorrelate(W):
    # Project W to the nearest orthonormal matrix (stabilizes training)
    U, _, Vt = np.linalg.svd(W)
    return U @ Vt

def whiten(X):
    """
    X: (m, n)
    Returns Xw (m, n) whitened, plus params for optional unwhitening.
    """
    Xc = X - X.mean(axis=1, keepdims=True)
    n = Xc.shape[1]
    Sigma = (Xc @ Xc.T) / n

    d, E = np.linalg.eigh(Sigma)          # ascending
    idx = np.argsort(d)[::-1]             # descending
    d, E = d[idx], E[:, idx]

    D_inv_sqrt = np.diag(1.0 / np.sqrt(d + 1e-12))
    Xw = D_inv_sqrt @ E.T @ Xc
    return Xw

def infomax_ica(Xw, lr=0.02, epochs=150, batch_size=8192, seed=0):
    """
    Xw: (m, n) whitened mixtures.
    Returns W, S_hat = W Xw
    """
    rng = np.random.default_rng(seed)
    m, n = Xw.shape

    W = np.eye(m, dtype=np.float64)

    for ep in range(epochs):
        order = rng.permutation(n)
        for start in range(0, n, batch_size):
            idx = order[start:start+batch_size]
            Xb = Xw[:, idx]                 # (m, B)
            Y = W @ Xb                      # (m, B)
            G = sigmoid(Y)                  # (m, B)

            # Natural-gradient style Infomax update:
            # ΔW ∝ (I + (1 - 2g(Y))Y^T/B) W
            B = Xb.shape[1]
            Z = (1.0 - 2.0 * G) @ Y.T / B   # (m, m)
            dW = (np.eye(m) + Z) @ W

            W = W + lr * dW
            W = sym_decorrelate(W)

        if (ep + 1) % 25 == 0:
            print(f"epoch {ep+1}/{epochs} | det(W)={np.linalg.det(W):.4f} | ||W||_F={np.linalg.norm(W):.3f}")

    S_hat = W @ Xw
    return W, S_hat

In [153]:
# whiten mixtures
Xw = whiten(X)

# ICA
W_hat, S_hat = infomax_ica(Xw, lr=0.02, epochs=200, batch_size=8192, seed=0)

# normalize recovered components for playback
rec0 = S_hat[0] / (np.max(np.abs(S_hat[0])) + 1e-12)
rec1 = S_hat[1] / (np.max(np.abs(S_hat[1])) + 1e-12)


epoch 200/200 | det(W)=1.0000 | ||W||_F=1.414


In [154]:
def corr(a, b):
    a = a - a.mean()
    b = b - b.mean()
    return (a @ b) / (np.linalg.norm(a) * np.linalg.norm(b) + 1e-12)

c00 = abs(corr(rec0, s1))
c01 = abs(corr(rec0, s2))
c10 = abs(corr(rec1, s1))
c11 = abs(corr(rec1, s2))

print("abs corr matrix:")
print([[c00, c01],
       [c10, c11]])

# choose assignment
if c00 + c11 >= c01 + c10:
    prof_rec, stud_rec = rec0, rec1
    # fix sign
    if corr(prof_rec, s1) < 0: prof_rec = -prof_rec
    if corr(stud_rec, s2) < 0: stud_rec = -stud_rec
else:
    prof_rec, stud_rec = rec1, rec0
    if corr(prof_rec, s1) < 0: prof_rec = -prof_rec
    if corr(stud_rec, s2) < 0: stud_rec = -stud_rec


abs corr matrix:
[[np.float64(0.0015625423114553197), np.float64(0.999999099217771)], [np.float64(0.9999992645081996), np.float64(0.0017002931805899751)]]


In [155]:
print("Recovered professor-like:")
display(Audio(prof_rec, rate=sr))

In [156]:
print("Recovered student-like:")
display(Audio(stud_rec, rate=sr))

## Visualizations (GeeksForGeeks-style)

We’ll plot:
1. Raw mixed signals (mic1 vs mic2) scatter
2. Recovered sources scatter
3. Waveforms for a short window

In [157]:
# Take a short slice for readable plots
T = min(8000, n)
x1 = Xw[0, :T]
x2 = Xw[1, :T]
r1 = prof_rec[:T]
r2 = stud_rec[:T]

plt.figure(figsize=(6,5))
plt.scatter(x1, x2, s=6, alpha=0.35)
plt.title("Whitened mixtures scatter: (mic1 vs mic2)")
plt.xlabel("Xw[0]")
plt.ylabel("Xw[1]")
plt.show()


In [158]:
plt.figure(figsize=(6,5))
plt.scatter(r1, r2, s=6, alpha=0.35, color="orange")
plt.title("Recovered sources scatter")
plt.xlabel("Recovered 1")
plt.ylabel("Recovered 2")
plt.show()

In [159]:
plt.figure(figsize=(10,4))
plt.plot(prof_rec[:T], label="Recovered professor-like", alpha=0.9)
plt.plot(stud_rec[:T], label="Recovered student-like", alpha=0.9)
plt.title("Recovered waveforms (short window)")
plt.xlabel("Sample")
plt.ylabel("Amplitude")
plt.legend()
plt.show()

## Key Takeaways

- PCA **reduces dimensionality** by preserving variance. ICA is different: it tries to recover **independent** latent sources.
- ICA needs **multiple mixed observations** (e.g., multiple microphones).  
  With only one mixture, you generally can’t separate two speakers.
- Whitening (a PCA step) makes ICA training **much more stable**.
- The simple update here is a direct implementation of the lecture-style gradient ascent:
  - it’s not the fastest
  - it’s good for learning + transparency
- Outputs are only identifiable up to **permutation and scaling**. That’s normal.

### If your separation still sounds “off”
Try:
- increasing `epochs` to 6–10
- lowering `lr` to 0.005–0.01
- selecting different professor/student wav pairs (some overlap more cleanly than others)